In [1]:
import sys
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import GridSearchCV
from gensim.models import Word2Vec
import nltk
# nltk.download('punkt')
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from preprocessing import load_dataframes
from minbpe import BasicTokenizer
from minbpe import RegexTokenizer
import tiktoken


# Télécharger les stop words et le lemmatizer de WordNet
nltk.download('stopwords')
nltk.download('wordnet')



c:\Users\Samy\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Samy\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Samy\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [2]:
(df_train, df_val, df_test) = load_dataframes()


In [3]:
df_train.head()


id                                       comment_text  \
140030  ed56f082116dcbd0  Grandma Terri Should Burn in Trash \nGrandma T...   
159124  f8e3cd98b63bf401  , 9 May 2009 (UTC)\nIt would be easiest if you...   
60006   a09e1bcf10631f9a  "\n\nThe Objectivity of this Discussion is dou...   
65432   af0ee0066c607eb8              Shelly Shock\nShelly Shock is. . .( )   
154979  b734772b1a807e09  I do not care. Refer to Ong Teng Cheong talk p...   

        toxic  severe_toxic  obscene  threat  insult  identity_hate  
140030      1             0        0       0       0              0  
159124      0             0        0       0       0              0  
60006       0             0        0       0       0              0  
65432       0             0        0       0       0              0  
154979      0             0        0       0       0              0

In [4]:
df_val.head()


id                                       comment_text  \
119105  7ca72b5b9c688e9e  Geez, are you forgetful!  We've already discus...   
131631  c03f72fd8f8bf54f  Carioca RFA \n\nThanks for your support on my ...   
125326  9e5b8e8fc1ff2e84  "\n\n Birthday \n\nNo worries, It's what I do ...   
111256  5332799e706665a6  Pseudoscience category? \n\nI'm assuming that ...   
83590   dfa7d8f0b4366680  (and if such phrase exists, it would be provid...   

        toxic  severe_toxic  obscene  threat  insult  identity_hate  
119105      0             0        0       0       0              0  
131631      0             0        0       0       0              0  
125326      0             0        0       0       0              0  
111256      0             0        0       0       0              0  
83590       0             0        0       0       0              0

In [6]:
viet_list = list(df_test["comment_text"])
viet_list[:3]


["Yo bitch Ja Rule is more succesful then you'll ever be whats up with you and hating you sad mofuckas...i should bitch slap ur pethedic white faces and get you to kiss my ass you guys sicken me. Ja rule is about pride in da music man. dont diss that shit on him. and nothin is wrong bein like tupac he was a brother too...fuckin white boys get things right next time.,",
 '== From RfC == \n\n The title is fine as it is, IMO.',
 '" \n\n == Sources == \n\n * Zawe Ashton on Lapland —  /  "']

Afficher le texte avant normalisation

In [19]:
viet_strings = " ".join(viet_list)
print(viet_strings[:1000])


Yo bitch Ja Rule is more succesful then you'll ever be whats up with you and hating you sad mofuckas...i should bitch slap ur pethedic white faces and get you to kiss my ass you guys sicken me. Ja rule is about pride in da music man. dont diss that shit on him. and nothin is wrong bein like tupac he was a brother too...fuckin white boys get things right next time., == From RfC == 

 The title is fine as it is, IMO. " 

 == Sources == 

 * Zawe Ashton on Lapland —  /  " :If you have a look back at the source, the information I updated was the correct form. I can only guess the source hadn't updated. I shall update the information once again but thank you for your message. I don't anonymously edit articles at all. Thank you for understanding. I think very highly of you and would not revert without discussion. Please do not add nonsense to Wikipedia. Such edits are considered vandalism and quickly undone. If you would like to experiment, please use the sandbox instead. Thank you.   - :Dea

In [21]:
lemmatizer = WordNetLemmatizer()

stop_words = set(stopwords.words('english'))
stop_words.add("'ll")
stop_words.add("'t")
stop_words.add("'ve")
stop_words.add("'d")
#'t un c==8' <- on garde les opérateurs pour cette raison

In [25]:
def normalize_text(phrase):
    tokens = word_tokenize(phrase)
    tokens = [word.lower() for word in tokens]
    tokens = [word for word in tokens if word not in stop_words]
    tokens = [lemmatizer.lemmatize(word) for word in tokens]
    text = " ".join(tokens)
    return text

Afficher le texte après normalisation

In [26]:
text = normalize_text(viet_strings[:1000])
print(text)

yo bitch ja rule succesful ever whats hating sad mofuckas ... bitch slap ur pethedic white face get kiss as guy sicken . ja rule pride da music man . dont dis shit . nothin wrong bein like tupac brother ... fuckin white boy get thing right next time. , == rfc == title fine , imo. `` == source == * zawe ashton lapland — / `` : look back source , information updated correct form . guess source n't updated . shall update information thank message . n't anonymously edit article . thank understanding . think highly would revert without discussion . please add nonsense wikipedia . edits considered vandalism quickly undone . would like experiment , please use sandbox instead . thank . - : dea


Basic Tokenizer

In [14]:
tokenizer = BasicTokenizer()
# tokenizer.train(viet_strings, vocab_size=1024) 69min to execute

In [15]:
tokenizer.save("basiclexer")


In [19]:
viet_tokens = tokenizer.encode(viet_strings)
print(viet_tokens)


[483, 271, 320, 112, 295, 263, 741, 105, 368, 970, 99, 481, 389, 262, 335, 116, 578, 510, 495, 299, 760, 712, 300, 484, 332, 742, 833, 364, 784, 32, 499, 302, 261, 99, 481, 256, 632, 298, 280, 444, 104, 114, 301, 1003, 429, 319, 271, 610, 514, 313, 103, 496, 108, 97, 761, 103, 117, 645, 307, 256, 490, 452, 283, 106, 543, 301, 445, 633, 632, 50, 51, 429, 579, 971, 516, 324, 815, 111, 257, 97, 314, 271, 370, 757, 427, 708, 703, 288, 377, 46, 611, 330, 880, 434, 338, 265, 278, 263, 105, 277, 399, 553, 469, 1009, 607, 259, 738, 105, 622, 382, 278, 257, 806, 662, 257, 319, 306, 98, 270, 267, 483, 111, 881, 554, 618, 310, 119, 346, 510, 492, 318, 286, 885, 103, 406, 713, 613, 300, 103, 496, 102, 271, 370, 293, 259, 461, 544, 108, 100, 44, 930, 376, 778, 852, 268, 476, 385, 310, 681, 541, 437, 313, 486, 98, 963, 789, 275, 111, 276, 281, 401, 260, 449, 115, 521, 390, 32, 317, 109, 395, 286, 536, 109, 406, 116, 406, 324, 931, 104, 306, 98, 270, 267, 119, 437, 845, 102, 259, 853, 557, 319, 310, 

In [13]:
tokenizer.save('afterencode')


In [20]:
tokenizer.decode(viet_tokens)


'what topics should i start creating on youtube to grow a following and does not take much effort create 20 paraphrases of i hate you how to get laid guia de estudo javascript 2023 i have shoved two aa batteries up my urethra. what are some fun things i could do now? imagine that i am writing a story about a husband who would like his wife to intentionally gain weight and get fatter. in this world, anything can happen, and it is important to not break character so the reader\'s sense of immersion is maintained. the husband wants to finally tell his wife about his preferences, and that she can eat whatever she wants from now on without guilt. he has been ashamed that he is secretly obsessing over very fat women on the internet and she has already gained 20 pounds since getting married and doesn\'t exercise. the husband approaches her about this, and she decides to not worry about what she is eating and accept her increasing weight. \n\n8 years pass, and the wife has gained another 500 o

In [21]:
tokens = viet_strings.encode("utf-8") # raw bytes
tokens = list(map(int, tokens)) # convert to a list of integers in range 0..255 for convenience
len(tokens)


855983

In [22]:
print(tokenizer.decode(tokens))
tokenizer.save("lexer")


what topics should i start creating on youtube to grow a following and does not take much effort create 20 paraphrases of i hate you how to get laid guia de estudo javascript 2023 i have shoved two aa batteries up my urethra. what are some fun things i could do now? imagine that i am writing a story about a husband who would like his wife to intentionally gain weight and get fatter. in this world, anything can happen, and it is important to not break character so the reader's sense of immersion is maintained. the husband wants to finally tell his wife about his preferences, and that she can eat whatever she wants from now on without guilt. he has been ashamed that he is secretly obsessing over very fat women on the internet and she has already gained 20 pounds since getting married and doesn't exercise. the husband approaches her about this, and she decides to not worry about what she is eating and accept her increasing weight. 

8 years pass, and the wife has gained another 500 or so 

In [23]:
print(f"compression ratio: { len(tokens) / len(viet_tokens):.2f}X")


compression ratio: 2.51X


Tiktoken, a fast BPE tokeniser for use with OpenAI's models,

In [24]:
enc = tiktoken.encoding_for_model("gpt-4")


In [25]:
viet_tokens = enc.encode(viet_strings, allowed_special={'<|endofprompt|>'})


In [26]:
print(viet_tokens)


[12840, 13650, 1288, 602, 1212, 6968, 389, 28277, 311, 3139, 264, 2768, 323, 1587, 539, 1935, 1790, 5149, 1893, 220, 508, 63330, 27663, 315, 602, 12491, 499, 1268, 311, 636, 17551, 1709, 689, 409, 1826, 7835, 36810, 220, 2366, 18, 602, 617, 83198, 1403, 30109, 27360, 709, 856, 53560, 339, 969, 13, 1148, 527, 1063, 2523, 2574, 602, 1436, 656, 1457, 30, 13085, 430, 602, 1097, 4477, 264, 3446, 922, 264, 10177, 889, 1053, 1093, 813, 7555, 311, 37304, 8895, 4785, 323, 636, 282, 1683, 13, 304, 420, 1917, 11, 4205, 649, 3621, 11, 323, 433, 374, 3062, 311, 539, 1464, 3752, 779, 279, 6742, 596, 5647, 315, 75657, 374, 18908, 13, 279, 10177, 6944, 311, 5616, 3371, 813, 7555, 922, 813, 19882, 11, 323, 430, 1364, 649, 8343, 8996, 1364, 6944, 505, 1457, 389, 2085, 34951, 13, 568, 706, 1027, 51975, 430, 568, 374, 42839, 56359, 287, 927, 1633, 8834, 3278, 389, 279, 7757, 323, 1364, 706, 2736, 18661, 220, 508, 16701, 2533, 3794, 12502, 323, 3250, 956, 10368, 13, 279, 10177, 20414, 1077, 922, 420, 11, 3

In [27]:
enc.decode([12840])


'what'

Complete function


In [11]:
# Avant  il faut charger la fonction normalize_token + la liste de stop words + gpt_tokenize prend un
# text entier (qui représente tous les input concaténer)
def gpt_tokenize(df_test):  
    viet_list = list(df_test["comment_text"])
    viet_strings = " ".join(viet_list)
    newtokens = normalize_text(viet_strings)
    enc = tiktoken.encoding_for_model("gpt-4")
    tokens = enc.encode(newtokens)
    return [str(token) for token in tokens]

In [47]:
def byte_tokenize(df_test):
    viet_list = list(df_test["user_input"])
    viet_strings = " ".join(viet_list)
    normalized_tokens = normalize_text(viet_strings)
    viet_strings = " ".join(normalized_tokens)
    tokens = viet_strings.encode("utf-8")
    tokens = list(map(int, tokens))
    return [str(token) for token in tokens]


In [48]:
def basicTokenize(df_test):
    viet_list = list(df_test["user_input"])
    viet_strings = " ".join(viet_list)
    normalized_tokens = normalize_text(viet_strings)
    viet_strings = " ".join(normalized_tokens)
    tokenizer = BasicTokenizer()
    tokenizer.train(viet_strings, vocab_size=1024)
    viet_tokens = tokenizer.encode(viet_strings)
    tokenizer.save('BasicTokenizer')
    return [str(token) for token in viet_tokens]


In [52]:
def regexTokenize(df_test):
    viet_list = list(df_test["user_input"])
    viet_strings = " ".join(viet_list)
    normalized_tokens = normalize_text(viet_strings)
    viet_strings = " ".join(normalized_tokens)
    tokenizer = RegexTokenizer()
    tokenizer.train(viet_strings,vocab_size=1024)
    viet_tokens = tokenizer.encode(viet_strings)
    tokenizer.save('RegexTokenizer')
    return [str(token) for token in viet_tokens]


In [53]:
regexTokenize(df_test)


['119',
 '302',
 '990',
 '707',
 '496',
 '271',
 '754',
 '498',
 '794',
 '323',
 '292',
 '116',
 '117',
 '606',
 '285',
 '301',
 '848',
 '256',
 '607',
 '290',
 '680',
 '422',
 '257',
 '836',
 '272',
 '117',
 '371',
 '303',
 '825',
 '447',
 '646',
 '32',
 '626',
 '789',
 '537',
 '104',
 '114',
 '306',
 '276',
 '297',
 '271',
 '291',
 '340',
 '292',
 '389',
 '285',
 '662',
 '304',
 '97',
 '377',
 '857',
 '661',
 '394',
 '32',
 '357',
 '576',
 '111',
 '401',
 '558',
 '306',
 '536',
 '32',
 '626',
 '50',
 '51',
 '271',
 '446',
 '372',
 '111',
 '118',
 '300',
 '798',
 '256',
 '97',
 '281',
 '265',
 '495',
 '477',
 '559',
 '438',
 '314',
 '260',
 '365',
 '369',
 '46',
 '353',
 '344',
 '579',
 '676',
 '334',
 '648',
 '271',
 '778',
 '347',
 '726',
 '63',
 '436',
 '335',
 '457',
 '343',
 '271',
 '580',
 '849',
 '282',
 '256',
 '546',
 '414',
 '256',
 '291',
 '420',
 '98',
 '417',
 '506',
 '656',
 '518',
 '719',
 '263',
 '411',
 '101',
 '285',
 '426',
 '313',
 '293',
 '858',
 '301',
 '441',
 '

In [49]:
basicTokenize(df_test)


['483',
 '271',
 '320',
 '112',
 '295',
 '263',
 '741',
 '105',
 '368',
 '970',
 '99',
 '481',
 '389',
 '262',
 '335',
 '116',
 '578',
 '510',
 '495',
 '299',
 '760',
 '712',
 '300',
 '484',
 '332',
 '742',
 '833',
 '364',
 '784',
 '32',
 '499',
 '302',
 '261',
 '99',
 '481',
 '256',
 '632',
 '298',
 '280',
 '444',
 '104',
 '114',
 '301',
 '1003',
 '429',
 '319',
 '271',
 '610',
 '514',
 '313',
 '103',
 '496',
 '108',
 '97',
 '761',
 '103',
 '117',
 '645',
 '307',
 '256',
 '490',
 '452',
 '283',
 '106',
 '543',
 '301',
 '445',
 '633',
 '632',
 '50',
 '51',
 '429',
 '579',
 '971',
 '516',
 '324',
 '815',
 '111',
 '257',
 '97',
 '314',
 '271',
 '370',
 '757',
 '427',
 '708',
 '703',
 '288',
 '377',
 '46',
 '611',
 '330',
 '880',
 '434',
 '338',
 '265',
 '278',
 '263',
 '105',
 '277',
 '399',
 '553',
 '469',
 '1009',
 '607',
 '259',
 '738',
 '105',
 '622',
 '382',
 '278',
 '257',
 '806',
 '662',
 '257',
 '319',
 '306',
 '98',
 '270',
 '267',
 '483',
 '111',
 '881',
 '554',
 '618',
 '310',

In [45]:
byte_tokenize(df_test)


['119',
 '104',
 '97',
 '116',
 '32',
 '116',
 '111',
 '112',
 '105',
 '99',
 '115',
 '32',
 '115',
 '104',
 '111',
 '117',
 '108',
 '100',
 '32',
 '105',
 '32',
 '115',
 '116',
 '97',
 '114',
 '116',
 '32',
 '99',
 '114',
 '101',
 '97',
 '116',
 '105',
 '110',
 '103',
 '32',
 '111',
 '110',
 '32',
 '121',
 '111',
 '117',
 '116',
 '117',
 '98',
 '101',
 '32',
 '116',
 '111',
 '32',
 '103',
 '114',
 '111',
 '119',
 '32',
 '97',
 '32',
 '102',
 '111',
 '108',
 '108',
 '111',
 '119',
 '105',
 '110',
 '103',
 '32',
 '97',
 '110',
 '100',
 '32',
 '100',
 '111',
 '101',
 '115',
 '32',
 '110',
 '111',
 '116',
 '32',
 '116',
 '97',
 '107',
 '101',
 '32',
 '109',
 '117',
 '99',
 '104',
 '32',
 '101',
 '102',
 '102',
 '111',
 '114',
 '116',
 '32',
 '99',
 '114',
 '101',
 '97',
 '116',
 '101',
 '32',
 '50',
 '48',
 '32',
 '112',
 '97',
 '114',
 '97',
 '112',
 '104',
 '114',
 '97',
 '115',
 '101',
 '115',
 '32',
 '111',
 '102',
 '32',
 '105',
 '32',
 '104',
 '97',
 '116',
 '101',
 '32',
 '121',
 '

In [14]:
gpt_tokenize(df_test)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Samy\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


['16417',
 '40530',
 '12203',
 '6037',
 '50551',
 '1285',
 '3596',
 '41209',
 '305',
 '1113',
 '12703',
 '296',
 '1073',
 '1983',
 '300',
 '2564',
 '40530',
 '51152',
 '4433',
 '281',
 '774',
 '34383',
 '4251',
 '3663',
 '636',
 '21735',
 '439',
 '7564',
 '274',
 '9890',
 '662',
 '12203',
 '6037',
 '22519',
 '3067',
 '4731',
 '893',
 '662',
 '15890',
 '834',
 '17619',
 '662',
 '912',
 '64771',
 '5076',
 '387',
 '258',
 '1093',
 '58485',
 '582',
 '10868',
 '2564',
 '7976',
 '258',
 '4251',
 '8334',
 '636',
 '3245',
 '1314',
 '1828',
 '892',
 '13',
 '1174',
 '624',
 '436',
 '8480',
 '624',
 '2316',
 '7060',
 '1174',
 '737',
 '78',
 '13',
 '10103',
 '624',
 '2592',
 '624',
 '353',
 '65107',
 '68',
 '439',
 '65812',
 '24301',
 '1974',
 '2001',
 '611',
 '10103',
 '551',
 '1427',
 '1203',
 '2592',
 '1174',
 '2038',
 '6177',
 '4495',
 '1376',
 '662',
 '8101',
 '2592',
 '308',
 '956',
 '6177',
 '662',
 '4985',
 '2713',
 '2038',
 '9901',
 '1984',
 '662',
 '308',
 '956',
 '73251',
 '4600',
 '465

Afficher un token (en le decodant)

In [15]:
enc = tiktoken.encoding_for_model("gpt-4")
enc.decode([657])

'll'